In [1]:
from collections import defaultdict
import re
import unicodedata
import numpy as np

In [2]:
taxa = [l.strip('\n') for l in open('taxa_to_use.txt','r')]

Load the data:

In [3]:
acd = [l.strip('\n').split('\t') for l in open('acd_merged_reflex_aligned.tsv','r')]
acd = [l[1:] for l in acd]
acd = list(set([tuple(l) for l in acd]))
acd = [list(l) for l in acd]
acd = [l for l in acd if l[1] in taxa]

We keep track of word IDs that appear to be derived forms as opposed to inherited from an earlier ancestor:

In [4]:
root_word = {}
for l in acd:
    root_word[(l[6],l[7],l[8])] = (l[0],l[4],l[5])

root_word = defaultdict(list)
for l in acd:
    root_word[(l[0],l[4],l[5])].append((l[6],l[7],l[8]))

for k in root_word.keys():
    root_word[k] = set(root_word[k])

derived = {}
for k in root_word.keys():
    for v in root_word[k]:
        if ('-' in v[1] or '<' in v[1] or ' ' in v[1]) and v[1] != k[1] and (v[1].count('-') != k[1].count('-') or v[1].count('<') != k[1].count('<') or v[1].count(' ') != k[1].count(' ')):
            derived[v[0]] = '.'.join(['D',v[0],v[2],v[1]])
        else:
            derived[v[0]] = '.'.join(['N',k[0],k[2],k[1]])

In [5]:
acd[0:2]

[['31699',
  'taga1270',
  'kampí-kampí',
  'being on the same side in a conflict, etc.',
  '*kampi',
  'PPh',
  '9864',
  '*kampi',
  'PPh',
  'kampí-kampí',
  'kampí-kampí',
  'kampí'],
 ['28663',
  'irar1238',
  'uf',
  'to blow',
  '*upi',
  'PCEMP',
  '5833',
  '*upi',
  'PCEMP',
  'uf',
  'uf',
  'uf']]

In [6]:
formdict = defaultdict(list)

for l in acd[1:]:
    etym_id = l[0]
    lang = l[1]
    word_id = l[6]
    form = l[9]
    gloss = l[3]
    aligned_morph = l[11]
    form = re.sub(r'(.)\1+',r'\1',form)
    aligned_morph = re.sub(r'(.)\1+',r'\1',aligned_morph)
    formdict[(etym_id,lang)].append((word_id,form,gloss,aligned_morph))

In [7]:
cons = ['B', 'C', 'D', 'G', 'H', 'K', 'L', 'M', 'N', 'P', 'R', 'S', 'T', 'V', 'W', 'X', 'Z', 'b', 'c', 'd', 'f', 'g', 'h', 'j', 'k', 'l', 'm', 'n', 'p', 'q', 'r', 's', 't', 'v', 'w', 'x', 'y', 'z', 'ð', 'ñ', 'č', 'đ', 'ń', 'ņ', 'ŋ', 'ŕ', 'š', 'ž', 'ƀ', 'ƚ', 'ǥ', 'ǵ', 'Ɂ', 'ɖ', 'ɗ', 'ɣ', 'ɫ', 'ɬ', 'ɭ', 'ɮ', 'ɸ', 'ʃ', 'ʄ', 'ʈ', 'ʔ', 'ʰ', 'ʷ', 'ʸ', 'β', 'γ', 'θ', 'ϕ', 'ᵇ', 'ᵏ', 'ᵐ', 'ᵬ', 'ḍ', 'ḏ', 'ḱ', 'ḷ', 'ḿ', 'ṁ', 'ṃ', 'ṇ', 'ṕ', 'ṛ', 'ṭ']

In [8]:
stringdict = defaultdict(list)
for k in formdict.keys():
    if len(formdict[k]) > 1:
        strings = []
        for v in formdict[k]:
            w = v[1]
            w = unicodedata.normalize('NFD',w).replace('́','')
            w = re.sub('<.*>','',w)
            w = w.replace('-','').replace(' ','')
            w = re.sub(r'(.)\1+',r'\1',w) #get rid of identical consonants across hyphens
            strings.append('#'+w+'$')
            #print(w)
        morphs = []
        for v in formdict[k]:
            w = v[3]
            w = unicodedata.normalize('NFD',w).replace('́','')
            w = re.sub('<.*>','',w)
            #morphs.append(w)
            morphs.append(''.join([s for s in re.sub(r'(.)\1+',r'\1',w) if s in cons]))
        morphs = set(morphs)
        #words = [v[1].replace('-','').replace(' ','') for v in formdict[k]]
        words = [v[1] for v in formdict[k]]
        substr = defaultdict(int)
        for string in strings:
            string_ = '#'+''.join([s for s in re.sub(r'(.)\1+',r'\1',string) if s in cons])+'$'
            #string_ = 
            for i in range(len(string_)):
                for j in range(i,len(string_)):
                    substr[string_[i:j+1]] += 1
        #substr = sorted([k for k in substr.keys() if substr[k] == max(substr.values())],key=lambda x:len(x))
        substr_ = sorted([k for k in substr.keys() if substr[k] >= len(strings) and len([m for m in morphs if m in k]) > 0],key=lambda x:len(x))
        if substr_ != []:
            longest = substr_[-1]
            for v in formdict[k]:
                stringdict[(derived[v[0]],k[1],v[0])].append(longest)
        else:
            longest = [''.join([s for s in w if s in cons]) for w in words if '-' not in w and ' ' not in w and '<' not in w]
            #for i,v in enumerate(formdict[k]):
            #    stringdict[(k[1],v[0])] = longest[i]
            for v in formdict[k]:
                stringdict[(derived[v[0]],k[1],v[0])] += longest
        #print(k,formdict[k])
        #print(longest)
    else:
        longest = ''.join([s for s in formdict[k][0][1] if s in cons])
        stringdict[(derived[formdict[k][0][0]],k[1],formdict[k][0][0])].append(longest)

for key in stringdict.keys():
    stringdict[key] = sorted(set(stringdict[key]))

In [9]:
#find the aligned full-word reflex for each record
wordform = {}
for l in acd:
    wordform[(l[1],l[6])] = l[10]

In [10]:
wholerecord = {}
for l in acd:
    wholerecord[(l[1],l[6])] = l[9]

In [11]:
for key in stringdict.keys():
    print(key,stringdict[key],wordform[(key[1],key[2])])

('N.28663.PCEMP.*upi', 'irar1238', '5833') ['f'] uf
('N.28321.PAN.*supsup', 'bang1368', '5426') ['ssp'] ba-susup
('N.27568.PWMP.*qalesem', 'pamp1243', '4164') ['slm'] pan-aslám
('D.4165.PWMP.*ma-qalesem', 'pamp1243', '4165') ['slm'] m-aslám
('N.30713.PWMP.*suŋsuŋ₁', 'cebu1242', '8300') ['slŋsŋ'] s<al>uŋsuŋ
('N.30777.PAN.*sikux', 'tali1262', '8485') ['sk'] siku
('N.31119.PPh.*banisah', 'ivat1242', '9093') ['bns', 'vnsh'] banisa
('N.27645.PAN.*qaSelu', 'paiw1248', '4303') ['qsl'] qaselu
('D.883.PWMP.*maŋ-belaq', 'java1254', '883') ['blh', 'mlh'] melah
('N.25286.PAN.*belaq', 'java1254', '879') ['blh', 'mlh'] belah
('N.33780.PMP.*buR(e)hu', 'cebu1242', '12558') ['bghn'] bughu-an
('N.31699.PPh.*kampi', 'taga1270', '9864') ['kmp'] kampí
('D.9865.PPh.*k<um>ampi', 'taga1270', '9865') ['kmp'] k<um>ampí
('N.30098.PAN.*SameCi', 'tsou1248', '6818') ['mc'] mici
('N.32158.PMP.*tuRaŋ', 'sang1336', '10419') ['thŋ'] tuhaŋ
('N.32962.PPh.*lusiq', 'mans1262', '11438') ['lsʔ'] lósiʔ
('N.26609.PAN.*kaCu', '

('N.28190.PWMP.*sepet₃', 'mala1479', '5191') ['#knspt$'] sepet
('D.861.PWMP.*ma-bekelaj', 'tont1239', '861') ['wlr$'] ma-welar
('N.25272.PMP.*bekelaj', 'tont1239', '856') ['wlr$'] welar
('N.24773.PAN.*aCay', 'kwai1243', '40') ['m'] mae-sia
('D.48.POC.*paka-mate-ia', 'kwai1243', '48') ['m'] faʔa-mae-a
('D.44.POC.*mate-qaŋa', 'kwai1243', '44') ['m'] mae-ŋa
('N.30979.PWMP.*pilis', 'java1254', '8879') ['mls', 'pls'] pilis
('N.25402.PWMP.*beŋeR', 'mina1268', '1071') ['bŋr'] baŋar
('N.25379.PAN.*beties', 'kela1258', '1035') ['bt'] beti
('D.4640.PMP.*ma-qudip', 'sout2859', '4640') ['ml'] me-ul
('N.32700.PPh.*umah', 'pamp1243', '11112') ['#m'] uma
('D.11113.PPh.*umah-an', 'pamp1243', '11113') ['#m'] uma-n
('N.28187.PAN.*Sepat', 'biak1248', '5163') ['fk'] fiak
('N.30421.PPh.*pílit', 'taga1270', '7555') ['plt'] ma-mílit
('N.28679.PWMP.*maka-', 'bont1247', '5863') ['mk'] maka-
('N.31395.PMP.*sakay₄', 'tong1325', '9490') ['hk$'] ha-hake
('N.31655.PPh.*kamiá', 'taga1270', '9811') ['kmy'] kamyá
('N.

('N.31948.PPh.*kal(e)bit', 'bont1247', '10165') ['#klbt'] kalbít
('N.29851.PAN.*batux', 'cebu1242', '6486') ['bt'] batú
('D.6493.PWMP.*batu-en', 'cebu1242', '6493') ['bt'] batu-un
('D.6495.PMP.*batu-batu', 'cebu1242', '6495') ['bt'] batu-bátu
('D.6491.PWMP.*b<um>atu', 'cebu1242', '6491') ['bt'] mu-batú
('N.30585.PMP.*Ribu', 'tugu1245', '7973') ['rhnh'] rihu-n
('D.8039.PMP.*kaen kaen', 'hanu1241', '8039') ['kʔn'] kaʔun-káʔun
('N.30603.PAN.*kaen', 'hanu1241', '8008') ['kʔn'] káʔun
('D.8013.PMP.*ma-ŋaen', 'hanu1241', '8013') ['kʔn'] ma-ŋáʔun
('D.8033.PAN.*kaen-en', 'hanu1241', '8033') ['kʔn'] kánʔ-un
('D.8015.PAN.*pa-kaen', 'hanu1241', '8015') ['kʔn'] mag-pa-káʔun
('D.8027.PAN.*k<um>aen', 'hanu1241', '8027') ['kʔn'] k<um>áʔun
('D.6577.PAN.*k<um>iRim', 'sais1237', '6577') ['#kLm$'] k<om>iLim
('N.29907.PAN.*kiRim', 'sais1237', '6575') ['#kLm$'] kiLim
('N.25075.PAN.*baliw₂', 'hanu1241', '560') ['lw$'] báliw
('N.31130.PAN.*(q)uNah', 'kulo1237', '9110') ['l'] ula
('D.9111.PAN.*(q)<um>uNah', 'k

('N.27960.PWMP.*raŋkaŋ', 'mina1268', '4845') ['rŋkŋ'] raŋkaŋ
('N.33832.PPh.*basag', 'mara1404', '12642') ['bsg'] basag
('N.31825.PWMP.*kumpul', 'mapu1244', '10017') ['kmp', 'ŋmp'] ka-kumpoh-an
('N.28117.PAN.*Sapuy', 'weje1237', '5037') ['p'] api
('N.30199.PPh.*dálaw', 'pamp1243', '7028') ['#dl$'] d<um>álo
('N.30495.PAN.*kaRaw₁', 'sika1262', '7723') ['gr'] garo
('D.4133.PMP.*X₃ + qatay', 'mala1479', '4133') ['ht'] hati
('D.4127.PMP.*buaq ni qatay', 'mala1479', '4127') ['ht'] hati
('D.4130.PWMP.*qulu ni qatay', 'mala1479', '4130') ['ht'] hati
('D.4136.PMP.*X₆ + qatay', 'mala1479', '4136') ['ht'] hati
('D.4135.PMP.*X₅ + qatay', 'mala1479', '4135') ['ht'] hati
('N.27555.PAN.*qaCay', 'mala1479', '4125') ['ht'] hati
('D.4134.PMP.*X₄ + qatay', 'mala1479', '4134') ['ht'] hati
('D.4131.PMP.*X₁ + qatay', 'mala1479', '4131') ['ht'] hati
('D.4132.PMP.*X₂ + qatay', 'mala1479', '4132') ['ht'] hati
('D.4128.PMP.*qalap qatay', 'mala1479', '4128') ['ht'] hati
('N.32163.PPh.*takál₁', 'casi1235', '10426'

('N.30880.PMP.*teRas', 'goro1259', '8705') ['tht'] poʔo-toheto-lo
('N.30248.PAN.*Nihib', 'paiw1248', '7123') ['lʸv$'] lʸiv
('N.28294.PAN.*Suaji', 'woli1241', '5369') ['nd'] andi
('N.33395.POC.*motus', 'saaa1240', '12042') ['m$'] mou
('N.25129.PMP.*banua', 'maka1311', '631') ['bn$'] banoa
('N.32743.PWMP.*kidelap', 'ilok1237', '11179') ['#klp$'] kiláp
('N.32932.PPh.*lábag', 'cebu1242', '11400') ['#lbg$'] lábag
('N.27207.PAN.*-nu₁', 'sira1267', '3687') ['n$'] hi-no
('N.25311.PWMP.*benaR', 'sasa1249', '922') ['bnr$'] benar
('N.30390.PMP.*tales', 'bata1301', '7486') ['tls'] täläs
('N.30778.POC.*siku', 'renn1242', '8495') ['sk$'] haka-siku
('N.30980.PPh.*pis(e)ŋí', 'taus1251', '8880') ['psn', 'psŋ'] pisni
('N.25233.PMP.*baŋi₂', 'buru1303', '781') ['bŋh'] baŋi-h
('N.25935.PAN.*CumeS', 'east2447', '2121') ['tm'] tuma
('N.27195.PMP.*ñikñik', 'waro1242', '11941') ['#nn$'] nini
('N.27195.PMP.*ñikñik', 'waro1242', '3668') ['#nn$'] nini
('N.25730.PAN.*buqaya', 'bang1368', '1711') ['b'] buea
('N.303

...

('N.30289.PAN.*kuliC', 'gane1237', '7214') ['klt'] kulit
('N.26324.PWMP.*hekas', 'tont1239', '2642') ['ŋks'] eŋkas
('N.26710.PWMP.*kemkem₁', 'cebu1242', '3170') ['kmkm'] kumkúm
('N.31832.POC.*kau₂', 'mota1237', '10028') ['#k'] kau-t
('N.30952.PMP.*tusiq', 'naka1262', '8819') ['tr'] turi
('N.26709.PMP.*kemiq', 'mala1479', '3169') ['kmh'] kəmeh
('N.27194.PMP.*niket', 'mang1405', '3667') ['nkt'] niket
('N.27843.PMP.*qubi', 'ilok1237', '4625') ['b'] úbi
('N.26947.PMP.*lemek₂', 'kela1258', '3413') ['lmk'] lemek
('N.28287.PWMP.*siŋ(e)het', 'buka1261', '5353') ['sŋt'] siŋot
('N.27358.PMP.*pa-₁', 'moli1248', '3888') ['vl'] va-lua
('N.28155.PMP.*sakay₁', 'ibal1244', '5120') ['mnsky'] man-sakay
('N.28113.PAN.*Sapit', 'sund1252', '5025') ['hpt'] hapit
('N.28605.PMP.*ujan', 'tuva1244', '11904') ['t'] uta
('N.33251.PMP.*diŋdiŋ₂', 'mota1237', '11770') ['mmrr'] ma-ma-rir
('N.31200.PMP.*saRuk', 'mala1479', '9232') ['srk'] sarok
('N.31150.PWMP.*taŋgiRi', 'ilok1237', '9142') ['tŋgg'] taŋgígi
('N.30573.P

('N.28318.PAN.*SuNus', 'chuu1238', '5422') ['wn'] wúnú
('N.25590.PAN.*bubu₂', 'taga1270', '1366') ['bb'] búbo
('N.28190.PWMP.*sepet₃', 'mara1404', '5191') ['spt'] sepet
('N.31944.PMP.*guRun', 'motu1246', '11260') ['krkr'] kuru-kuru
('N.33783.POC.*ŋodro', 'raro1241', '12562') ['ŋr'] ŋoro
('N.26449.PMP.*ijuŋ', 'tong1325', '12510') ['h'] ihu-
('N.30131.PMP.*paqet', 'mala1479', '6870') ['pht'] pahat
('N.30377.PAN.*takut', 'katb1237', '7428') ['mtk'] matak
('N.33196.POC.*mapat', 'samo1305', '11698') ['mmf'] ma-mafa
('N.30365.PAN.*lima', 'taku1257', '7384') ['rm'] rima
('N.32583.PWMP.*pucuk', 'sasa1249', '10951') ['psk'] pusuk
('N.27471.PMP.*pucek', 'mang1405', '4014') ['pck'] pucek
('N.33792.POC.*bura₂', 'gela1263', '12579') ['mbr'] mbura
('N.29829.PAN.*baqi', 'amis1246', '6438') ['fʔ'] faʔi
('N.31827.PPh.*kúpit', 'casi1235', '10019') ['kpt'] kúpit
('N.27362.PAN.*paŋa₁', 'cebu1242', '3894') ['pŋ'] paŋá
('N.31675.PMP.*kepkep', 'mong1342', '9832') ['lkkp'] ali-kokop
('N.31124.PMP.*likuq', 'we

('N.25652.PMP.*bukuh', 'simb1256', '1515') ['pk'] puku
('D.9767.PMP.*i-kahu', 'lamb1273', '9767') ['y'] y-au
('N.27897.PMP.*quruŋ', 'banj1239', '4742') ['hrŋ'] huruŋ
('N.26922.PWMP.*la(m)paw', 'mara1404', '3387') ['lpw'] lapaw
('N.26314.PMP.*haŋin', 'kili1267', '2617') ['ygl'] yagila
('N.32427.PPh.*tariktik₁', 'mara1404', '10754') ['trntk'] tarintik
('N.26312.PWMP.*haŋak', 'bugh1239', '12531') ['ŋ'] aŋa
('N.28690.PWMP.*utus₂', 'bata1289', '5883') ['tsn'] utus-an
('N.31552.POC.*see', 'east2447', '9677') ['s'] sē
('N.26390.PMP.*hutek', 'sasa1249', '2745') ['tk'] otak
('N.24779.PWMP.*adu', 'java1254', '75') ['d'] adu
('N.25237.PWMP.*baŋkulis', 'maka1311', '785') ['bŋklsʔ'] baŋkulisiʔ
('N.33237.POC.*laka₂', 'muss1246', '11754') ['lk'] laka
('N.31860.POC.*kua kua', 'gela1263', '10060') ['k'] kua
('D.3713.PMP.*ma-nuRuq', 'samo1305', '3713') ['mn'] manū
('N.31251.PWMP.*subuk₁', 'iban1264', '9299') ['sbk'] subok
('N.27295.PMP.*paniki', 'bata1298', '3809') ['pnʔ'] panniʔ
('N.30453.PAN.*susu₁', 

('N.26356.PWMP.*hinzam', 'pamp1243', '2688') ['ndm'] indám
('N.33289.PPh.*ludlud₁', 'bont1247', '11817') ['ldld'] ludlud
('N.30482.PAN.*duma', 'atay1247', '7685') ['rmʔ'] rumaʔ
('N.27760.PMP.*qezen', 'sund1252', '4506') ['hjn'] (h)ɨjɨn
('N.28689.PMP.*utus₁', 'cham1312', '5882') ['gts'] gutos
('N.24873.PAN.*aRi', 'rapa1244', '7827') ['m'] mai
('N.30256.PAN.*nipen', 'tagb1258', '7136') ['npn'] nipɨn
('N.25312.PWMP.*benaŋ', 'nias1242', '923') ['bn'] bõna
('N.25190.PAN.*basbas₂', 'taga1270', '722') ['bsbs'] basbás
('N.33373.PPh.*dáyaw', 'cebu1242', '11979') ['dyw'] dáyaw
('N.30240.PAN.*layu', 'gayo1244', '7111') ['ly'] layu
('N.27859.PAN.*qulej', 'west2555', '7200') ['ld'] uled
('N.25730.PAN.*buqaya', 'kwai1243', '1713') ['fl'] fuala
('N.25542.PAN.*bitbit₁', 'mala1479', '1279') ['bbt'] bibit
('N.25293.PMP.*belaŋ₂', 'goro1259', '891') ['hlŋ'] hulaŋo
('N.32261.POC.*topo', 'bugh1239', '10552') ['ttp'] to-topo
('D.10989.PPh.*linis-en', 'ivat1242', '10989') ['lnsn'] linis-en
('N.33962.PAN.*pahp

('N.32042.PPh.*taq₁', 'isna1241', '10274') ['t'] ta
('N.25657.PMP.*bulan-bulan₁', 'cebu1242', '1532') ['blnbln'] bulan-búlan
('N.30532.PMP.*kima', 'cala1258', '7811') ['km'] kima
('N.31332.POC.*sumu', 'hawa1245', '9407') ['hmhm'] humu-humu
('N.26354.PPh.*himatún', 'pang1290', '2686') ['mtn'] imatón
('N.25493.PWMP.*binuaŋ', 'sund1252', '1207') ['bnŋ'] binuaŋ
('N.30486.PMP.*taq₃', 'sang1336', '7691') ['t'] ta
('N.28111.PAN.*sapaw', 'idaa1241', '5020') ['spw'] sapow
('D.10387.POC.*qanus-i', 'emae1237', '10387') ['ns'] nusi
('N.30671.PAN.*SeReC', 'mong1342', '8209') ['gtn'] ogot-an
('D.7846.PMP.*ma-taqu₂', 'hano1246', '7846') ['mwt'] mwatua
('N.33697.PPh.*sa(ŋ)kab', 'west2555', '12445') ['skb'] sakab
('N.30026.POC.*lilim', 'samo1305', '6722') ['ll'] lili
('N.30793.PPh.*duldúl₁', 'taga1270', '8526') ['dldl'] duldól
('N.26398.PPh.*huñat', 'ilok1237', '2755') ['nt'] unnát
('N.33093.PPh.*lábis', 'hanu1241', '11584') ['lbs'] lábis
('N.27836.POC.*qono₂', 'niue1239', '4611') ['n'] ono
('N.30846.P

In [12]:
coding = {}
for k in stringdict.keys():
    lang = k[1]
    if lang not in coding.keys():
        coding[lang] = defaultdict(list)
    for w in stringdict[k]:
        if re.sub(r'(.)\1+',r'\1',w) != w:
            coding[lang][k[0]].append('1')
        else:
            coding[lang][k[0]].append('0')

In [13]:
coding = {}
for k in stringdict.keys():
    lang = k[1]
    if lang not in coding.keys():
        coding[lang] = defaultdict(list)
    for w in stringdict[k]:
        c = ''
        if re.sub(r'(.)\1+',r'\1',w) != w:
            c += '1 '
            #coding[lang][k[0]].append('1')
        else:
            c += '0 '
            #coding[lang][k[0]].append('0')
        word = ''.join([s for s in wordform[(k[1],k[2])] if s in cons])
        if re.sub(r'(.)\1+',r'\1',word) != word:
            c += '1'
        else:
            c += '0'
        coding[lang][k[0]].append(c)
        if c == '1 0':
            print(k,stringdict[k],wordform[(k[1],k[2])],'\t',wholerecord[(k[1],k[2])])

('D.10576.PMP.*tuktuk-i', 'hawa1245', '10576') ['kk'] kuʔ-i 	 kuʔ-i
('N.26872.PMP.*laki₁', 'meri1243', '3334') ['lh', 'llhy'] láhi 	 láhi
('D.9027.PWMP.*ma-nutu', 'meri1243', '9027') ['tt'] ma-noto 	 ma-noto
('N.31517.PWMP.*suan', 'bata1289', '9638') ['nn'] na 	 ama na s<um>uan ahu
('D.7627.PWMP.*ma-ñusu', 'mala1479', '7627') ['ss'] me-ñusu 	 me-ñusu
('N.27867.PAN.*quluh', 'mala1479', '4674') ['hl', 'ltt'] hulu 	 hulu
('D.4680.PWMP.*paŋ-qulu', 'mala1479', '4680') ['hl', 'ltt'] peŋ-hulu 	 peŋ-hulu
('D.4683.PMP.*qulu ni batu', 'mala1479', '4683') ['hl', 'ltt'] batu 	 kepala batu
('D.4677.PMP.*di qulu', 'mala1479', '4677') ['hl', 'ltt'] da-hulu 	 da-hulu
('D.1375.PMP.*bubuŋ-an', 'mala1479', '1375') ['bbŋ', 'bmbŋ'] bumboŋ-an 	 bumboŋ-an
('N.25594.PMP.*bubuŋ₁', 'mala1479', '1374') ['bbŋ', 'bmbŋ'] bumboŋ 	 bumboŋ lima
('N.26759.PMP.*kik', 'mang1405', '3219') ['hk', 'kk'] hik 	 hik
('D.8392.PWMP.*ma-naytay', 'pala1344', '8392') ['dd'] mə-líd 	 mə-líd
('N.25576.PAN.*buaq', 'pulu1242', '1333') 

('D.9442.PPh.*l<um>aja', 'west2557', '9442') ['#ll$'] l<um>ala 	 l<um>ala
('D.9441.PPh.*l<in>ága', 'west2557', '9441') ['#ll$'] l<in>ala 	 l<in>ala
('N.30010.PAN.*dapaN', 'ivat1242', '6919') ['rpnnlm'] rapan 	 rapan no lima
('N.30744.PMP.*taytay', 'tont1239', '8390') ['#tt$'] t<um>ete 	 t<um>ete
('N.27425.PWMP.*pikat', 'mala1479', '3964') ['mmkt'] p<em>ikat 	 p<em>ikat
('N.30558.PAN.*duSa', 'sela1259', '7875') ['rrr'] ru 	 ru
('N.32561.PWMP.*purpur', 'sasa1249', '10924') ['mpr', 'ppr'] mupur 	 mupur
('N.33762.POC.*d(r)amut', 'muss1246', '12538') ['rrmt'] ai 	 ai ra-ramut-i
('N.31338.PWMP.*piket₂', 'isna1241', '9418') ['mmkt', 'pkt'] píkat 	 píkat
('N.26533.PAN.*isa₁', 'meri1243', '2965') ['ss'] isa 	 isa
('D.2969.PAN.*isa isa', 'meri1243', '2969') ['ss'] isa 	 tsi-isa isa
('D.8629.PMP.*mata nu susu', 'keii1239', '8629') ['ssmtn'] mata-n 	 sus mata-n
('D.8295.PWMP.*ma-ñuksuk', 'mala1479', '8295') ['ssk'] me-ñusok 	 me-ñusok
('N.27393.PWMP.*pekpek₂', 'sasa1249', '3930') ['mpk', 'ppk'] me

In [14]:
coding = {}
for k in stringdict.keys():
    lang = k[1]
    if lang not in coding.keys():
        coding[lang] = defaultdict(list)
    for w in stringdict[k]:
        val = 'none'
        word = wordform[(k[1],k[2])]
        word = re.sub(r'(.)\1+',r'\1',word)
        word = ''.join([s for s in word if s in cons])
        if re.sub(r'(.)\1+',r'\1',word) != word:
            val = 'word'
        if re.sub(r'(.)\1+',r'\1',w) != w:
            val = 'morph'
        coding[lang][k[0]].append(val)
        print(k,stringdict[k],w,word,val)

('N.28663.PCEMP.*upi', 'irar1238', '5833') ['f'] f f none
('N.28321.PAN.*supsup', 'bang1368', '5426') ['ssp'] ssp bssp morph
('N.27568.PWMP.*qalesem', 'pamp1243', '4164') ['slm'] slm pnslm none
('D.4165.PWMP.*ma-qalesem', 'pamp1243', '4165') ['slm'] slm mslm none
('N.30713.PWMP.*suŋsuŋ₁', 'cebu1242', '8300') ['slŋsŋ'] slŋsŋ slŋsŋ none
('N.30777.PAN.*sikux', 'tali1262', '8485') ['sk'] sk sk none
('N.31119.PPh.*banisah', 'ivat1242', '9093') ['bns', 'vnsh'] bns bns none
('N.31119.PPh.*banisah', 'ivat1242', '9093') ['bns', 'vnsh'] vnsh bns none
('N.27645.PAN.*qaSelu', 'paiw1248', '4303') ['qsl'] qsl qsl none
('D.883.PWMP.*maŋ-belaq', 'java1254', '883') ['blh', 'mlh'] blh mlh none
('D.883.PWMP.*maŋ-belaq', 'java1254', '883') ['blh', 'mlh'] mlh mlh none
('N.25286.PAN.*belaq', 'java1254', '879') ['blh', 'mlh'] blh blh none
('N.25286.PAN.*belaq', 'java1254', '879') ['blh', 'mlh'] mlh blh none
('N.33780.PMP.*buR(e)hu', 'cebu1242', '12558') ['bghn'] bghn bghn none
('N.31699.PPh.*kampi', 'taga127

('N.30427.PAN.*demdem₂', 'loni1238', '7568') ['']   none
('N.25072.PWMP.*baliuŋ', 'ngaj1237', '552') ['blŋ'] blŋ blŋ none
('N.27295.PMP.*paniki', 'pang1290', '3809') ['pnk'] pnk pnk none
('N.27609.PAN.*qaNiŋu', 'mans1262', '4234') ['nn'] nn nn morph
('N.31179.PMP.*saput₁', 'taga1270', '9195') ['spt'] spt spt none
('D.9196.PWMP.*saput-an', 'taga1270', '9196') ['spt'] spt sptn none
('N.27285.PMP.*panahik', 'mong1342', '3791') ['pnk'] pnk pnk none
('N.28583.PMP.*uaʔ', 'pamo1252', '5710') ['']   none
('N.24785.POC.*ai₁', 'raro1241', '82') ['']   none
('N.30758.PMP.*saRman', 'gilb1244', '8454') ['rm'] rm rm none
('N.27139.POC.*bio', 'chek1238', '3609') ['b'] b b none
('N.30410.PAN.*luluj', 'bint1246', '7542') ['lld'] lld lld morph
('N.31508.PAN.*saput₂', 'ivat1242', '9629') ['sptn'] sptn sptn none
('D.2908.PWMP.*indu-ŋ', 'sund1252', '2908') ['ndŋ$'] ndŋ$ ndŋ none
('D.7779.PMP.*taŋis-taŋis', 'bata1289', '7779') ['tŋs'] tŋs tŋstŋs none
('N.25887.PAN.*Caŋis', 'bata1289', '2040') ['tŋs'] tŋs tŋ

('N.30830.PAN.*maCa', 'taga1270', '8602') ['mt'] mt mmtʔn word
('D.8604.PPh.*pa-matá', 'taga1270', '8604') ['mt'] mt pmt none
('D.8609.PPh.*mata-en', 'taga1270', '8609') ['mt'] mt mthn none
('N.27859.PAN.*qulej', 'pulu1242', '7200') ['wl'] wl wl none
('N.32589.PPh.*luás', 'pang1290', '10967') ['ls'] ls ls none
('N.27323.PMP.*para', 'ilok1237', '3843') ['pr'] pr pr none
('N.26728.PWMP.*kerus₁', 'mara1404', '3188') ['krs'] krs krs none
('N.30470.POC.*koki', 'hawa1245', '7665') ['ʔʔ$'] ʔʔ$ hʔʔ morph
('N.31068.PPh.*taqul', 'taus1251', '9024') ['tl$'] tl$ tml none
('N.28722.PMP.*wahiR', 'ujir1237', '5919') ['wy'] wy wy none
('N.28469.PAN.*tepuk', 'mang1405', '5593') ['#tmpk$'] #tmpk$ tmpk none
('N.27692.PMP.*qazay', 'mong1342', '4391') ['yy'] yy yy morph
('N.25378.PWMP.*beteŋ₂', 'maka1311', '1034') ['btŋ$'] btŋ$ btŋ none
('N.25750.PAN.*buReS', 'casi1235', '1752') ['#bg'] #bg bg none
('D.1754.PMP.*buRah-an', 'casi1235', '1754') ['#bg'] #bg bgn none
('N.31185.PPh.*sapsáp', 'cent2089', '9207'

('D.8419.PWMP.*in-telu', 'timu1262', '8419') ['tl'] tl ntl none
('N.30461.PMP.*kunij', 'meri1243', '7652') ['hntr'] hntr hntr none
('N.27960.PWMP.*raŋkaŋ', 'mina1268', '4845') ['rŋkŋ'] rŋkŋ rŋkŋ none
('N.33832.PPh.*basag', 'mara1404', '12642') ['bsg'] bsg bsg none
('N.31825.PWMP.*kumpul', 'mapu1244', '10017') ['kmp', 'ŋmp'] kmp kkmphn word
('N.31825.PWMP.*kumpul', 'mapu1244', '10017') ['kmp', 'ŋmp'] ŋmp kkmphn word
('N.28117.PAN.*Sapuy', 'weje1237', '5037') ['p'] p p none
('N.30199.PPh.*dálaw', 'pamp1243', '7028') ['#dl$'] #dl$ dml none
('N.30495.PAN.*kaRaw₁', 'sika1262', '7723') ['gr'] gr gr none
('D.4133.PMP.*X₃ + qatay', 'mala1479', '4133') ['ht'] ht ht none
('D.4127.PMP.*buaq ni qatay', 'mala1479', '4127') ['ht'] ht ht none
('D.4130.PWMP.*qulu ni qatay', 'mala1479', '4130') ['ht'] ht ht none
('D.4136.PMP.*X₆ + qatay', 'mala1479', '4136') ['ht'] ht ht none
('D.4135.PMP.*X₅ + qatay', 'mala1479', '4135') ['ht'] ht ht none
('N.27555.PAN.*qaCay', 'mala1479', '4125') ['ht'] ht ht none
('

('N.30668.PMP.*salaq₁', 'cebu1242', '8193') ['slʔ'] slʔ slʔ none
('D.8204.PWMP.*salaq-an', 'cebu1242', '8204') ['slʔ'] slʔ sdʔn none
('D.8199.PMP.*pa(ka)-salaq', 'cebu1242', '8199') ['slʔ'] slʔ pksdʔn none
('N.33189.PPh.*labag', 'taga1270', '11690') ['#lbg$'] #lbg$ lmbg none
('N.28722.PMP.*wahiR', 'asss1237', '5919') ['wʔ'] wʔ wʔ none
('N.25245.PMP.*bakas₁', 'maka1311', '806') ['bŋksʔ'] bŋksʔ bŋksʔ none
('N.25294.PMP.*belbel₁', 'mang1405', '894') ['bbl'] bbl bbl morph
('N.32202.PWMP.*tuŋkus', 'indo1316', '10474') ['tŋks'] tŋks tŋks none
('N.25291.PPh.*belay', 'mara1404', '889') ['bly$'] bly$ blbly none
('N.28566.PWMP.*tugtug', 'ivat1242', '5694') ['tgtg'] tgtg tgtg none
('D.8966.PPh.*tugtug-én', 'ivat1242', '8966') ['tgtg'] tgtg tgtgn none
('N.26780.PAN.*kiSkiS', 'paiw1248', '3240') ['krsks'] krsks krsks none
('N.30513.PCMP.*masu', 'mamb1306', '7742') ['msn'] msn msn none
('D.7893.PAN.*paka-duSa', 'paiw1248', '7893') ['ds$'] ds$ pkḍs none
('N.30558.PAN.*duSa', 'paiw1248', '7874') ['ds$

...

('N.27252.PMP.*palak', 'mina1268', '3754') ['plk'] plk plk none
('N.27758.PMP.*qeti₃', 'tong1325', '4496') ['ʔs'] ʔs ʔs none
('N.28631.PWMP.*umbak umbak', 'mara1404', '5792') ['mbkmbk'] mbkmbk mbkmbk none
('N.30354.PAN.*timuRmuR', 'puyu1239', '7347') ['TmRmR'] TmRmR TmRmR none
('N.31952.PWMP.*kurapu', 'taga1270', '10171') ['klp'] klp klp none
('N.28242.PMP.*simbuR', 'casi1235', '5279') ['sbgsbg'] sbgsbg sbgsbg none
('N.28640.PMP.*umpu', 'tali1262', '5802') ['h'] h h none
('N.33403.PAN.*deŋdeŋ₂', 'paiw1248', '12084') ['zlŋzŋ'] zlŋzŋ zlŋzŋ none
('N.27843.PMP.*qubi', 'urav1235', '4625') ['np'] np np none
('N.27874.PMP.*qumpan', 'bint1246', '4705') ['pn'] pn pn none
('N.31076.PPh.*salugsúg', 'casi1235', '9035') ['slgsg'] slgsg slgsg none
('N.30944.PMP.*saŋa₁', 'gilb1244', '8805') ['rŋ'] rŋ rŋ none
('N.30230.PAN.*dalem', 'inab1237', '7108') ['llm'] llm llm morph
('N.32965.PPh.*lutáq', 'ivat1242', '11442') ['xt'] xt xt none
('N.30143.PMP.*ñamuk', 'anut1237', '6887') ['nm'] nm nm none
('N.322

('N.32520.PAN.*piNay', 'hanu1241', '10862') ['ply'] ply ply none
('N.30259.PPh.*paypáy', 'binu1244', '7141') ['pypy'] pypy pypy none
('N.28330.PMP.*surup₁', 'pamo1252', '5445') ['sy'] sy sy none
('N.31704.PWMP.*kaya', 'ilok1237', '9870') ['ky'] ky ky none
('D.7787.PAN.*um-ala', 'bugi1244', '7787') ['ml'] ml ml none
('N.32563.PWMP.*puspus₃', 'mala1479', '10927') ['pps'] pps pps morph
('N.31214.PMP.*sukun', 'java1254', '9247') ['skn'] skn skn none
('N.32354.PMP.*taRin', 'hanu1241', '10663') ['tgn'] tgn tgn none
('N.27643.PAN.*qasawa', 'wuvu1239', '4294') ['r'] r r none
('N.32517.PWMP.*padem', 'mapu1244', '10859') ['pwm'] pwm pwm none
('N.24944.PAN.*a₄', 'atay1247', '381') ['']   none
('N.30928.PAN.*si₁', 'cent2101', '8782') ['s'] s s none
('N.29860.PWMP.*kiray', 'cent2089', '6508') ['kly'] kly kly none
('N.26856.PMP.*ku(n)tus', 'buru1303', '3319') ['kth'] kth kth none
('N.31088.PPh.*iba', 'casi1235', '9055') ['b'] b b none
('N.30576.PMP.*Rumbia', 'sang1336', '7959') ['hmb'] hmb hmb none


('N.31392.PMP.*suŋkit', 'renn1242', '9485') ['sk'] sk sk none
('N.30932.PAN.*mu-', 'thao1240', '8789') ['m'] m m none
('N.30459.PAN.*kuCux', 'meke1243', '7641') ['ʔ'] ʔ ʔ none
('N.30186.PAN.*peNuq', 'reja1241', '6986') ['pn'] pn pn none
('N.30641.POC.*sipo', 'toab1237', '8150') ['#sf$'] #sf$ sf none
('N.27112.PMP.*mekmek', 'motu1246', '3582') ['mm'] mm mm morph
('N.32822.PPh.*luk(e)tún', 'ilok1237', '11274') ['lktn'] lktn lktn none
('N.30453.PAN.*susu₁', 'east2447', '7625') ['']   none
('N.26019.PAN.*dikit', 'hawa1245', '10066') ['lʔ'] lʔ lʔ none
('N.30976.PWMP.*ŋazel', 'kela1258', '8874') ['ŋdl'] ŋdl ŋdl none
('N.26830.PAN.*kuris₁', 'sund1252', '3290') ['krs'] krs krs none
('N.26663.PMP.*kaRuki', 'kosr1238', '3122') ['klk'] klk klk none
('N.31826.PWMP.*kupiŋ', 'java1254', '10018') ['kpŋ'] kpŋ kpŋ none
('N.27624.PAN.*qapid', 'bont1247', '4264') ['ʔpd'] ʔpd ʔpd none
('N.25715.PMP.*buntul', 'cebu1242', '1668') ['bntl'] bntl bntl none
('N.33009.PPh.*liput₂', 'ilok1237', '11495') ['lpt'] l

('N.32299.PWMP.*tayug', 'iban1264', '10599') ['tyk'] tyk tyk none
('N.32625.PWMP.*puntuk', 'taus1251', '11018') ['pntk'] pntk pntk none
('N.27421.PWMP.*picuk', 'mala1479', '3959') ['pck'] pck pck none
('N.31070.PAN.*tutuh', 'leti1246', '9026') ['tt'] tt tt morph
('N.25480.PMP.*binaŋa', 'mong1342', '1188') ['bnŋ'] bnŋ bnŋ none
('N.30950.PWMP.*sejem', 'mong1342', '8814') ['tym'] tym tym none
('N.32309.PPh.*tuleŋ', 'boto1242', '10609') ['tlŋ'] tlŋ tlŋ none
('N.28068.PWMP.*sabaqaŋ', 'mala1479', '4955') ['swŋ'] swŋ swŋ none
('N.27348.PAN.*paspas₁', 'kava1241', '3877') ['pmsps'] pmsps pmsps none
('N.28069.PMP.*sabaŋ₁', 'binu1244', '4956') ['sbŋ'] sbŋ sbŋ none
('N.25114.PAN.*baNaS', 'tunj1244', '615') ['wn'] wn wn none
('N.30661.PAN.*lawaq₂', 'nort2836', '8178') ['kl'] kl kl none
('N.24834.PAN.*aNak', 'sais1237', '183') ['ʔlk'] ʔlk ʔlk none
('D.7601.PMP.*ma-zaqat', 'bugi1244', '7601') ['mjʔ'] mjʔ mjʔ none
('N.27913.PMP.*quzuŋ', 'yamd1240', '4797') ['nd'] nd nd none
('N.28773.PPh.*witwít₂', 'c

('N.25700.PMP.*bunbun', 'cebu1242', '1642') ['bnbn'] bnbn bnbn none
('N.30668.PMP.*salaq₁', 'sika1261', '8193') ['sl'] sl sl none
('N.24851.PAN.*-an', 'atay1247', '254') ['n'] n n none
('N.25027.PWMP.*balanak', 'iban1264', '500') ['blnk'] blnk blnk none
('N.32134.POC.*nofo', 'motu1246', '10388') ['nh'] nh nh none
('N.27522.PCEMP.*bail', 'mang1405', '4072') ['fl'] fl fl none
('N.30924.POC.*mana', 'ghar1239', '8772') ['mn'] mn mn none
('N.33487.PPh.*ukap', 'mans1262', '12208') ['kp'] kp kp none
('N.30776.PMP.*sawa', 'taga1270', '8484') ['sw'] sw sw none
('N.33030.PMP.*malem', 'buka1261', '11519') ['mlm'] mlm mlm none
('N.32189.PWMP.*tadu', 'hanu1241', '10460') ['tr'] tr tr none
('N.27033.PWMP.*li(ŋ)get', 'sasa1249', '3503') ['lŋgt'] lŋgt lŋgt none
('D.8138.PWMP.*ma-naRaq', 'pamo1252', '8138') ['mntʔ'] mntʔ mntʔ none
('N.30938.PAN.*di', 'lamp1243', '8796') ['d'] d d none
('N.25724.PMP.*bunut₁', 'bugh1239', '1699') ['vnñ'] vnñ vnñ none
('N.28453.PWMP.*temud', 'west2555', '5577') ['tmdmd'] 

In [15]:
langs_to_keep = [lang for lang in coding.keys() if len(coding[lang].keys()) > 100]

L = len(langs_to_keep)

coding_ = {}
for lang in coding.keys():
    if lang in langs_to_keep:
        coding_[lang] = coding[lang]

coding = coding_

In [16]:
cogvar = defaultdict(list)
for lang in coding.keys():
    for k in coding[lang].keys():
        cogvar[k] += coding[lang][k]

for k in cogvar.keys():
    cogvar[k] = sorted(set(cogvar[k]))

In [17]:
coglang = defaultdict(list)
for lang in coding.keys():
    for k in coding[lang].keys():
        coglang[k].append(lang)

#cogs_to_keep = [k for k in coglang.keys() if len(cogvar[k]) > 1 and len(coglang[k])>5]
cogs_to_keep = [k for k in coglang.keys() if len(coglang[k])>10]

colnames = ['']
charvalues = []

print(L,len(cogs_to_keep))

124 905


In [18]:
for cog in cogs_to_keep:
    names = ['absent','none','morph','word']
    vals = np.zeros([L,len(names)])
    for lang in langs_to_keep:
        if cog in coding[lang].keys():
            for v in coding[lang][cog]:
                vals[langs_to_keep.index(lang),names.index(v)] = 1
        else:
            vals[langs_to_keep.index(lang),names.index('absent')] = 1
    colnames += [cog+':'+''.join(n) for n in names]
    charvalues.append(vals)

charvalues = np.concatenate(charvalues,-1)

In [19]:
f = open('../data/character_data.tsv','w')
print('\t'.join(colnames),file=f)
for i,lang in enumerate(langs_to_keep):
    print('\t'.join([lang]+[str(s) for s in list(charvalues[i,])]),file=f)

f.close()

#cognate_attrs = {l[0]:[l[5],l[4]] for l in acd}

f = open('../data/cognate_key.tsv','w')
print('\t'.join(['cognate_ID','protolanguage','protoform']),file=f)
for cog in cogs_to_keep:
    print('\t'.join([cog]+cog.split('.')[-2:]),file=f)

f.close()

subgroups = defaultdict(list)
for l in acd:
    subgroups[l[5]].append(l[1])

f = open('../data/subgroup_key.tsv','w')
print('\t'.join(['']+list(subgroups.keys())),file=f)
for lang in langs_to_keep:
    print('\t'.join([lang]+['1' if lang in subgroups[k] else '0' for k in subgroups.keys()]),file=f)

f.close()


In [20]:
colnames

['',
 'N.28113.PAN.*Sapit:absent',
 'N.28113.PAN.*Sapit:none',
 'N.28113.PAN.*Sapit:morph',
 'N.28113.PAN.*Sapit:word',
 'N.30411.PAN.*luluN:absent',
 'N.30411.PAN.*luluN:none',
 'N.30411.PAN.*luluN:morph',
 'N.30411.PAN.*luluN:word',
 'N.25730.PAN.*buqaya:absent',
 'N.25730.PAN.*buqaya:none',
 'N.25730.PAN.*buqaya:morph',
 'N.25730.PAN.*buqaya:word',
 'N.27552.PMP.*qabuk:absent',
 'N.27552.PMP.*qabuk:none',
 'N.27552.PMP.*qabuk:morph',
 'N.27552.PMP.*qabuk:word',
 'N.25645.PAN.*bukeS:absent',
 'N.25645.PAN.*bukeS:none',
 'N.25645.PAN.*bukeS:morph',
 'N.25645.PAN.*bukeS:word',
 'N.24792.PAN.*aku:absent',
 'N.24792.PAN.*aku:none',
 'N.24792.PAN.*aku:morph',
 'N.24792.PAN.*aku:word',
 'N.30118.PMP.*miñak:absent',
 'N.30118.PMP.*miñak:none',
 'N.30118.PMP.*miñak:morph',
 'N.30118.PMP.*miñak:word',
 'N.30753.PAN.*telu:absent',
 'N.30753.PAN.*telu:none',
 'N.30753.PAN.*telu:morph',
 'N.30753.PAN.*telu:word',
 'N.25138.PMP.*baqbaq:absent',
 'N.25138.PMP.*baqbaq:none',
 'N.25138.PMP.*baqbaq:m